In [ ]:
# !pip install gradio evaluate datasets
# !pip install accelerate -U
# !pip install git+https://github.com/huggingface/transformers

In [ ]:
from datasets import load_dataset

gtzan = load_dataset("marsyas/gtzan", "all")
gtzan

In [ ]:
gtzan = gtzan["train"].train_test_split(seed=42, shuffle=True, test_size=0.1)
gtzan

In [ ]:
gtzan["train"][0]

In [ ]:
id2label_fn = gtzan["train"].features["genre"].int2str
id2label_fn(gtzan["train"][0]["genre"])

In [ ]:
#from IPython.display import Audio as displayAudio

#Audio(gtzan["train"][0]["audio"]["array"], rate=gtzan["train"][0]["audio"]["sampling_rate"])

In [ ]:
# import gradio as gr
# def generate_audio():
#     example = gtzan["train"].shuffle()[0]
#     audio = example["audio"]
#     return (
#         audio["sampling_rate"],
#         audio["array"],
#     ), id2label_fn(example["genre"])


# with gr.Blocks() as demo:
#     with gr.Column():
#         for _ in range(4):
#             audio, label = generate_audio()
#             output = gr.Audio(audio, label=label)

# demo.launch(debug=True)

In [ ]:
from transformers import AutoFeatureExtractor
from transformers import AutoConfig

model_id = "ntu-spml/distilhubert" #"NicolasDenier/distilhubert-finetuned-gtzan"

configuration = AutoConfig.from_pretrained(model_id)
configuration.hidden_dropout = 0.5
configuration.attention_dropout = 0.1

feature_extractor = AutoFeatureExtractor.from_pretrained(
    model_id, do_normalize=True, return_attention_mask=True, config=configuration
)

In [ ]:
sampling_rate = feature_extractor.sampling_rate
sampling_rate

In [ ]:
from datasets import Audio

gtzan = gtzan.cast_column("audio", Audio(sampling_rate=sampling_rate))
gtzan["train"][0]

In [ ]:
import numpy as np
import librosa
import random

test = gtzan["train"][4]

In [ ]:
def change_pitch(data, sampling_rate, pitch_factor):
    data =  np.asarray(data, dtype=np.float64)
    augmented_data = librosa.effects.pitch_shift(data, sr=sampling_rate, n_steps=pitch_factor)
    return augmented_data

def add_noise(data, noise_factor):
    data =  np.asarray(data, dtype=np.float64)
    noise = np.random.randn(len(data))
    augmented_data = data + noise_factor * noise
    # Cast back to same data type
    augmented_data = augmented_data.astype(type(data[0]))
    return augmented_data

def transform_data(data, sr=16000):
    # 1/2 chance of getting transformed
    if random.random()>0.6:
        data = np.asarray(data, dtype=np.float64)
        # random pitch in [-4,-2]U[2,4]
        pitch_factor = random.randint(2,4) *(1 if random.random()>0.5 else -1)
        data_augmented = change_pitch(data, sr, pitch_factor)
        # random noise in [0.05,0.2]
        noise_factor = random.random()*0.15+0.05
        data_augmented = add_noise(data_augmented, noise_factor)
        return data_augmented
    else:
        return data

transform_data_vect = np.vectorize(transform_data , signature='(n)->(n)')

test_pitch = change_pitch(test["audio"]["array"], sampling_rate, 8) # -4
test_noise = add_noise(test["audio"]["array"], 0.2)
test_pitch_noise = transform_data(test["audio"]["array"])

In [ ]:
#displayAudio(test_pitch_noise, rate=sampling_rate)

In [ ]:
# sample = gtzan["train"][0]["audio"]

# print(f"Mean: {np.mean(sample['array']):.3}, Variance: {np.var(sample['array']):.3}")

In [ ]:
# inputs = feature_extractor(sample["array"], sampling_rate=sample["sampling_rate"])

# print(f"inputs keys: {list(inputs.keys())}")

# print(
#     f"Mean: {np.mean(inputs['input_values']):.3}, Variance: {np.var(inputs['input_values']):.3}"
# )

In [ ]:
max_duration = 30.0

def preprocess_function(examples):
  audio_arrays = [x["array"] for x in examples["audio"]]
  inputs = feature_extractor(
      audio_arrays,
      sampling_rate=feature_extractor.sampling_rate,
      max_length=int(feature_extractor.sampling_rate * max_duration),
      truncation=True,
      padding=True,
      return_attention_mask=True,
  )
  return inputs

In [ ]:
gtzan_encoded = gtzan.map(
    preprocess_function, remove_columns=["audio", "file"], batched=True, num_proc=1, batch_size=100
)
gtzan_encoded

In [ ]:
gtzan_encoded = gtzan_encoded.rename_column("genre", "label")

In [ ]:
import copy
# copy the test dataset to not apply tranformations on it
gtzan_encoded_test = copy.deepcopy(gtzan_encoded['test'])

In [ ]:
def transform_batch(batch):
  augmented_data = transform_data_vect(batch["input_values"])
  augmented_batch = {'input_values': augmented_data}
  return augmented_batch

In [ ]:
# define a function that will be called when the data is accessed
gtzan_encoded.set_transform(transform_batch, columns="input_values", output_all_columns=True)

In [ ]:
id2label = {
    str(i): id2label_fn(i)
    for i in range(len(gtzan_encoded["train"].features["label"].names))
}
label2id = {v: k for k, v in id2label.items()}

id2label["7"]

In [ ]:
from transformers import AutoModelForAudioClassification

num_labels = len(id2label)

model = AutoModelForAudioClassification.from_pretrained(
    model_id,
    num_labels=num_labels,
    label2id=label2id,
    id2label=id2label,
)

In [ ]:
from huggingface_hub import notebook_login

notebook_login()

In [ ]:
from transformers import TrainingArguments

model_name = "distilhubert"
batch_size = 8
gradient_accumulation_steps = 1
num_train_epochs = 12

training_args = TrainingArguments(
    f"{model_name}-finetuned-gtzan",
    evaluation_strategy="epoch",
    save_strategy="epoch",
    learning_rate=5e-5,
    per_device_train_batch_size=batch_size,
    gradient_accumulation_steps=gradient_accumulation_steps,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=num_train_epochs,
    warmup_ratio=0.1,
    logging_steps=5,
    load_best_model_at_end=True,
    metric_for_best_model="accuracy",
    fp16=True,
    push_to_hub=True,
)

In [ ]:
import evaluate

metric = evaluate.load("accuracy")

def compute_metrics(eval_pred):
    """Computes accuracy on a batch of predictions"""
    predictions = np.argmax(eval_pred.predictions, axis=1)
    return metric.compute(predictions=predictions, references=eval_pred.label_ids)

In [ ]:
from transformers import Trainer

trainer = Trainer(
    model,
    training_args,
    train_dataset=gtzan_encoded["train"],
    eval_dataset=gtzan_encoded_test,
    tokenizer=feature_extractor,
    compute_metrics=compute_metrics,
)

trainer.train()

In [ ]:
kwargs = {
    "dataset_tags": "marsyas/gtzan",
    "dataset": "GTZAN",
    "model_name": f"{model_name}-finetuned-gtzan",
    "finetuned_from": model_id,
    "tasks": "audio-classification",
}

In [ ]:
trainer.push_to_hub(**kwargs)